In [2]:
import praw
import pandas as pd
import datetime
reddit = praw.Reddit(client_id='YKHyzDsxpKV0mg',
                     client_secret='Ph_adJuGZAkrt2vx8n5MSNCnaWc',
                     user_agent='scripto by /u/ninjamelons',
                     username='ninjamelons')
print(reddit.info)

<bound method Reddit.info of <praw.reddit.Reddit object at 0x000001CDE1E31EF0>>


In [3]:
import pymongo
mongoClient = pymongo.MongoClient("mongodb://localhost:27017/")
BigDb = mongoClient["BigData"]
redditDb = BigDb["reddit"]
redditDb

Collection(Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'BigData'), 'reddit')

Documents contain:
    Title
    text
    subreddit
    type of text
*or*
    Post title
    comment text
    subreddit
    type of text

In [4]:
posts = []

shortyStories = reddit.subreddit('ShortyStories').hot(limit=1000)
# dir(next(shortyStories)) #Check the variables that this object contains
for story in shortyStories:
    posts.append((datetime.datetime.utcfromtimestamp(story.created_utc),story.subreddit.display_name,story.title,story.selftext, 'shortstory'))

nosleepStories = reddit.subreddit('nosleep').hot(limit=1000)
for story in nosleepStories:
    posts.append((datetime.datetime.utcfromtimestamp(story.created_utc),story.subreddit.display_name,story.title,story.selftext, 'shortstory'))

sadStories = reddit.subreddit('ShortSadStories').hot(limit=1000)
for story in sadStories:
    posts.append((datetime.datetime.utcfromtimestamp(story.created_utc),story.subreddit.display_name,story.title,story.selftext, 'shortstory'))

hfyStories = reddit.subreddit('HFY').hot(limit=1000)
for story in hfyStories:
    posts.append((datetime.datetime.utcfromtimestamp(story.created_utc),story.subreddit.display_name,story.title,story.selftext, 'shortstory'))

wpromptStories = reddit.subreddit('writingprompts').hot(limit=1000)
# dir(next(writingPrompts).comments[0].submission) #Check the variables that this object contains
for submission in wpromptStories:
    submission.comments.replace_more(limit=0)
    for comment in submission.comments:
        posts.append((datetime.datetime.utcfromtimestamp(comment.created_utc),comment.subreddit.display_name,comment.submission.title,comment.body,'shortstory'))

promptstory = pd.DataFrame(posts, columns=['datetime','subreddit','title','body','type'])
promptstory.head(10), promptstory.tail(10)

(             datetime      subreddit  \
 0 2019-04-03 21:06:25  ShortyStories   
 1 2019-03-25 19:50:36  ShortyStories   
 2 2019-03-25 18:07:34  ShortyStories   
 3 2019-03-21 18:39:48  ShortyStories   
 4 2019-03-12 13:22:04  ShortyStories   
 5 2019-03-11 16:05:49  ShortyStories   
 6 2019-03-09 22:40:18  ShortyStories   
 7 2019-02-24 23:12:48  ShortyStories   
 8 2019-02-17 00:11:09  ShortyStories   
 9 2019-02-11 21:03:45  ShortyStories   
 
                                                title  \
 0                        [Fiction] Death is a friend   
 1                                           Doorways   
 2  Genuine Feedback Would Be Appreciated — Machin...   
 3                             Intro to my Noir Story   
 4  (Short Story) The Nomadian: The Mind of the Pupil   
 5                                  Ambiguity of Love   
 6                                   Midnight Visitor   
 7             [fiction] the sunsets on mars are blue   
 8                                

In [4]:
regex = "\*\*Welcome to the Prompt!\*\*"
filter = promptstory['body'].str.contains(regex)
filter.tail(10)

4849     True
4850     True
4851    False
4852    False
4853     True
4854    False
4855     True
4856     True
4857     True
4858    False
Name: body, dtype: bool

In [5]:
botless_df = promptstory[~filter]
botless_df.head()

datetime      subreddit  \
0 2019-04-03 21:06:25  ShortyStories   
1 2019-03-25 19:50:36  ShortyStories   
2 2019-03-25 18:07:34  ShortyStories   
3 2019-03-21 18:39:48  ShortyStories   
4 2019-03-12 13:22:04  ShortyStories   

                                               title  \
0                        [Fiction] Death is a friend   
1                                           Doorways   
2  Genuine Feedback Would Be Appreciated — Machin...   
3                             Intro to my Noir Story   
4  (Short Story) The Nomadian: The Mind of the Pupil   

                                                body        type  
0  Death is a friend.  Everyone is well acquainte...  shortstory  
1  &#x200B;\n\nI heard a knock at the door, but I...  shortstory  
2  So for the past 3 months I've been writing thi...  shortstory  
3  Preface: I have more written thus far however,...  shortstory  
4                                                     shortstory

In [6]:
import numpy as np
nandf = botless_df.replace('', np.nan, regex=False)
nandf = nandf.replace('[deleted]', np.nan, regex=False)
botless_df.head(), botless_df.tail(10)

(             datetime      subreddit  \
 0 2019-04-03 21:06:25  ShortyStories   
 1 2019-03-25 19:50:36  ShortyStories   
 2 2019-03-25 18:07:34  ShortyStories   
 3 2019-03-21 18:39:48  ShortyStories   
 4 2019-03-12 13:22:04  ShortyStories   
 
                                                title  \
 0                        [Fiction] Death is a friend   
 1                                           Doorways   
 2  Genuine Feedback Would Be Appreciated — Machin...   
 3                             Intro to my Noir Story   
 4  (Short Story) The Nomadian: The Mind of the Pupil   
 
                                                 body        type  
 0  Death is a friend.  Everyone is well acquainte...  shortstory  
 1  &#x200B;\n\nI heard a knock at the door, but I...  shortstory  
 2  So for the past 3 months I've been writing thi...  shortstory  
 3  Preface: I have more written thus far however,...  shortstory  
 4                                                     shortstory  ,

In [7]:
cleandf = nandf.dropna(inplace=False, axis=0)
cleandf['datetime'].apply(lambda x: x.strftime('%d%m%Y %H%M%S'))
cleandf.head()

datetime      subreddit  \
0 2019-04-03 21:06:25  ShortyStories   
1 2019-03-25 19:50:36  ShortyStories   
2 2019-03-25 18:07:34  ShortyStories   
3 2019-03-21 18:39:48  ShortyStories   
5 2019-03-11 16:05:49  ShortyStories   

                                               title  \
0                        [Fiction] Death is a friend   
1                                           Doorways   
2  Genuine Feedback Would Be Appreciated — Machin...   
3                             Intro to my Noir Story   
5                                  Ambiguity of Love   

                                                body        type  
0  Death is a friend.  Everyone is well acquainte...  shortstory  
1  &#x200B;\n\nI heard a knock at the door, but I...  shortstory  
2  So for the past 3 months I've been writing thi...  shortstory  
3  Preface: I have more written thus far however,...  shortstory  
5  Regret\n\nIt's the darkest of the night.Yet th...  shortstory

In [8]:
#redditDb is the mongoDb reddit collection instance
documentList = list()
for row in cleandf.itertuples():
    documentList.append({"datetime":row.datetime, "subreddit":row.subreddit, "title":row.title, "text":row.body, "type":row.type})

In [9]:
cleandf.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3964 entries, 0 to 4858
Data columns (total 5 columns):
datetime     3964 non-null datetime64[ns]
subreddit    3964 non-null object
title        3964 non-null object
body         3964 non-null object
type         3964 non-null object
dtypes: datetime64[ns](1), object(4)
memory usage: 185.8+ KB


In [10]:
documentList

[{'datetime': Timestamp('2019-04-03 21:06:25'),
  'subreddit': 'ShortyStories',
  'title': '[Fiction] Death is a friend',
  'text': "Death is a friend.  Everyone is well acquainted with his cold, inviting presence.  He is always there.  Every birthday, reminding you that it's a year closer to the end.  Every reunion, reminding you that someday everyone here will be dead.  Every funeral, reminding you that someday this will all be for you.  Though no one particularly likes death, we do owe a great deal to him.  Without Death we'd not have fear, our guiding compass.  Without him we'd not have love, for everything would be eternal.  Without him we'd not have purpose, because ones purpose is to complete or ensure something before the end.  So again I say, Death is a friend. ",
  'type': 'shortstory'},
 {'datetime': Timestamp('2019-03-25 19:50:36'),
  'subreddit': 'ShortyStories',
  'title': 'Doorways',
  'text': '&#x200B;\n\nI heard a knock at the door,\xa0but I looked out my window to an 

In [11]:
result = redditDb.insert_many(documentList)
result